In [42]:
# import course;course.header()
import pandas as pd


# Retrieve COVID data from ECDC 

In [43]:
covid_url = "https://opendata.ecdc.europa.eu/covid19/casedistribution/json/"
import ssl
ssl._create_default_https_context = ssl._create_unverified_context
import json
import urllib

In [44]:
covid_json_unformated = urllib.request.urlopen(covid_url).read().decode("utf-8")
covid_json = json.loads(covid_json_unformated)
cdf = pd.DataFrame(covid_json['records'])

In [45]:
cdf.sample(10)

dateRep day month  year  cases  deaths countriesAndTerritories  \
4702   01/09/2020  01    09  2020   2174      33              Bangladesh   
58611  25/04/2020  25    04  2020   5158    1010          United_Kingdom   
61747  20/08/2020  20    08  2020    265       9                Zimbabwe   
32515  15/06/2020  15    06  2020      0       0                  Latvia   
36404  18/11/2020  18    11  2020      3       0        Marshall_Islands   
37136  01/07/2020  01    07  2020   7143     648                  Mexico   
45443  24/10/2020  24    10  2020  13632     153                  Poland   
24476  20/03/2020  20    03  2020      1       0                Guernsey   
34969  21/11/2020  21    11  2020      1       0                  Malawi   
35778  01/05/2020  01    05  2020    191       1                Maldives   

      geoId countryterritoryCode  popData2019 continentExp  \
4702     BD                  BGD  163046173.0         Asia   
58611    UK                  GBR   66647112.0       Europe   
61747    ZW                  ZWE   14645473.0       Africa   
32515    LV                  LVA    1919968.0       Europe   
36404    MH                  MHL      58791.0      Oceania   
37136    MX                  MEX  127575529.0      America   
45443    PL                  POL   37972812.0       Europe   
24476    GG                  GGY      64468.0       Europe   
34969    MW                  MWI   18628749.0       Africa   
35778    MV                  MDV     530957.0         Asia   

      Cumulative_number_for_14_days_of_COVID-19_cases_per_100000  
4702                                         20.76221685          
58611                                        96.07468063          
61747                                         8.90377525          
32515                                         1.61461024          
36404                                         5.10282186          
37136                                        60.88706871          
45443                                       294.89520028          
24476                                                             
34969                                         0.32745087          
35778                                        83.43425174

In [46]:
cdf.shape

(61900, 12)

Rename columns to something more Pythonian. If you think they look already great, then at least rename `notification_rate_per_100000_population_14-days` to `14d-incidence`

In [47]:
cdf.rename(columns={
    "dateRep": "date", 
    "countriesAndTerritories": "countries", 
    "geoId": "2lettercode", 
    "countryterritoryCode": "3lettercode", 
    "popData2019": "population", 
    "continentExp": "continent", 
    "Cumulative_number_for_14_days_of_COVID-19_cases_per_100000": "14d-incidence"}, 
    inplace=True)
cdf.head()

date day month  year  cases  deaths    countries 2lettercode  \
0  14/12/2020  14    12  2020    746       6  Afghanistan          AF   
1  13/12/2020  13    12  2020    298       9  Afghanistan          AF   
2  12/12/2020  12    12  2020    113      11  Afghanistan          AF   
3  11/12/2020  11    12  2020     63      10  Afghanistan          AF   
4  10/12/2020  10    12  2020    202      16  Afghanistan          AF   

  3lettercode  population continent 14d-incidence  
0         AFG  38041757.0      Asia    9.01377925  
1         AFG  38041757.0      Asia    7.05277624  
2         AFG  38041757.0      Asia    6.86876792  
3         AFG  38041757.0      Asia    7.13426564  
4         AFG  38041757.0      Asia    6.96865815

Identify which columns have not been casted to an appropriate type during loading!

We did not cover datetime objects in pandas, however they are quite powerful!

Try:

In [48]:
cdf['date_reported'] = pd.to_datetime(cdf['year'] + "-" + cdf["month"] + "-" + cdf["day"])

Now you can treat the column as a datetime objects using `df[col].dt` , e.g. https://docs.python.org/3/library/datetime.html#datetime.date.year

In [49]:
cdf['date_reported'].dt.day.head()

0    14
1    13
2    12
3    11
4    10
Name: date_reported, dtype: int64

In [50]:
cdf.head()

date day month  year  cases  deaths    countries 2lettercode  \
0  14/12/2020  14    12  2020    746       6  Afghanistan          AF   
1  13/12/2020  13    12  2020    298       9  Afghanistan          AF   
2  12/12/2020  12    12  2020    113      11  Afghanistan          AF   
3  11/12/2020  11    12  2020     63      10  Afghanistan          AF   
4  10/12/2020  10    12  2020    202      16  Afghanistan          AF   

  3lettercode  population continent 14d-incidence date_reported  
0         AFG  38041757.0      Asia    9.01377925    2020-12-14  
1         AFG  38041757.0      Asia    7.05277624    2020-12-13  
2         AFG  38041757.0      Asia    6.86876792    2020-12-12  
3         AFG  38041757.0      Asia    7.13426564    2020-12-11  
4         AFG  38041757.0      Asia    6.96865815    2020-12-10

In [51]:
cdf = cdf.convert_dtypes()
for col in ["day", "month", "year", "14d-incidence"]:
    cdf[col] = pd.to_numeric(cdf[col])
cdf.dtypes

date                     string
day                       int64
month                     int64
year                      int64
cases                     Int64
deaths                    Int64
countries                string
2lettercode              string
3lettercode              string
population                Int64
continent                string
14d-incidence           float64
date_reported    datetime64[ns]
dtype: object

Create a new column `deltaTime_since_start_of_recording`

In [52]:
start_of_recording = min(cdf["date_reported"])
cdf["deltaTime_since_start_of_recording"] = cdf["date_reported"] - start_of_recording
cdf

date  day  month  year  cases  deaths    countries 2lettercode  \
0      14/12/2020   14     12  2020    746       6  Afghanistan          AF   
1      13/12/2020   13     12  2020    298       9  Afghanistan          AF   
2      12/12/2020   12     12  2020    113      11  Afghanistan          AF   
3      11/12/2020   11     12  2020     63      10  Afghanistan          AF   
4      10/12/2020   10     12  2020    202      16  Afghanistan          AF   
...           ...  ...    ...   ...    ...     ...          ...         ...   
61895  25/03/2020   25      3  2020      0       0     Zimbabwe          ZW   
61896  24/03/2020   24      3  2020      0       1     Zimbabwe          ZW   
61897  23/03/2020   23      3  2020      0       0     Zimbabwe          ZW   
61898  22/03/2020   22      3  2020      1       0     Zimbabwe          ZW   
61899  21/03/2020   21      3  2020      1       0     Zimbabwe          ZW   

      3lettercode  population continent  14d-incidence date_reported  \
0             AFG    38041757      Asia       9.013779    2020-12-14   
1             AFG    38041757      Asia       7.052776    2020-12-13   
2             AFG    38041757      Asia       6.868768    2020-12-12   
3             AFG    38041757      Asia       7.134266    2020-12-11   
4             AFG    38041757      Asia       6.968658    2020-12-10   
...           ...         ...       ...            ...           ...   
61895         ZWE    14645473    Africa            NaN    2020-03-25   
61896         ZWE    14645473    Africa            NaN    2020-03-24   
61897         ZWE    14645473    Africa            NaN    2020-03-23   
61898         ZWE    14645473    Africa            NaN    2020-03-22   
61899         ZWE    14645473    Africa            NaN    2020-03-21   

      deltaTime_since_start_of_recording  
0                               349 days  
1                               348 days  
2                               347 days  
3                               346 days  
4                               345 days  
...                                  ...  
61895                            85 days  
61896                            84 days  
61897                            83 days  
61898                            82 days  
61899                            81 days  

[61900 rows x 14 columns]

Create histograms for different columns or describe the df. Can you spot the inconsistency in the data? Fix it! :)

In [53]:
# cdf[["cases", "deaths", "14d-incidence"]] = abs(cdf[["cases", "deaths", "14d-incidence"]]) # no negative values

In [54]:
negative_values = cdf[["cases", "deaths", "14d-incidence"]] < 0
negative_values

cases  deaths  14d-incidence
0      False   False          False
1      False   False          False
2      False   False          False
3      False   False          False
4      False   False          False
...      ...     ...            ...
61895  False   False          False
61896  False   False          False
61897  False   False          False
61898  False   False          False
61899  False   False          False

[61900 rows x 3 columns]

In [55]:
for col in ["cases", "deaths", "14d-incidence"]:
    cdf = cdf.drop(cdf[cdf[col] < 0].index)

In [56]:
import plotly.express as px

for col_name in ["cases", "deaths", "14d-incidence"]:
    fig = px.histogram(cdf[col_name].dropna(), x=col_name, log_y=True)
    fig.show()

Identify those countries (grouped by continent) which showed the most drastic increase most drastic and decrease of the `14d-incidence` within the different years since recording. Visualize intuitively!

In [57]:
cdf = cdf.set_index(["continent", "countries"])
cdf = cdf.reset_index()
cdf.head()


continent    countries        date  day  month  year  cases  deaths  \
0      Asia  Afghanistan  14/12/2020   14     12  2020    746       6   
1      Asia  Afghanistan  13/12/2020   13     12  2020    298       9   
2      Asia  Afghanistan  12/12/2020   12     12  2020    113      11   
3      Asia  Afghanistan  11/12/2020   11     12  2020     63      10   
4      Asia  Afghanistan  10/12/2020   10     12  2020    202      16   

  2lettercode 3lettercode  population  14d-incidence date_reported  \
0          AF         AFG    38041757       9.013779    2020-12-14   
1          AF         AFG    38041757       7.052776    2020-12-13   
2          AF         AFG    38041757       6.868768    2020-12-12   
3          AF         AFG    38041757       7.134266    2020-12-11   
4          AF         AFG    38041757       6.968658    2020-12-10   

  deltaTime_since_start_of_recording  
0                           349 days  
1                           348 days  
2                           347 days  
3                           346 days  
4                           345 days

In [58]:
cdf_group = cdf[["continent", "countries", "14d-incidence"]].groupby(["continent", "countries"])
cdf_group.head()

continent    countries  14d-incidence
0          Asia  Afghanistan       9.013779
1          Asia  Afghanistan       7.052776
2          Asia  Afghanistan       6.868768
3          Asia  Afghanistan       7.134266
4          Asia  Afghanistan       6.968658
...         ...          ...            ...
61568    Africa     Zimbabwe       8.849151
61569    Africa     Zimbabwe       9.538784
61570    Africa     Zimbabwe       9.887014
61571    Africa     Zimbabwe       9.955295
61572    Africa     Zimbabwe      10.235245

[1070 rows x 3 columns]

In [59]:
import numpy as np
difference = cdf_group["14d-incidence"].apply(np.diff, axis=0)
max_increase = difference.apply(np.nanmax)
max_decrease = difference.apply(np.nanmin)

for continent in list(cdf["continent"].unique()):
    searched_max = max_increase[continent].sort_values(ascending=False).index[0]
    print("Max: " + continent + ": " + searched_max)

for continent in list(cdf["continent"].unique()):
    searched_min = max_decrease[continent].sort_values(ascending=True).index[0]
    print("Min: " + continent + ": " + searched_min)

Max: Asia: Kyrgyzstan
Max: Europe: Holy_See
Max: Africa: Equatorial_Guinea
Max: America: Falkland_Islands_(Malvinas)
Max: Oceania: French_Polynesia
Max: Other: Cases_on_an_international_conveyance_Japan
Min: Asia: Kyrgyzstan
Min: Europe: Holy_See
Min: Africa: Equatorial_Guinea
Min: America: Belize
Min: Oceania: French_Polynesia
Min: Other: Cases_on_an_international_conveyance_Japan


C:\Users\L\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.9_qbz5n2kfra8p0\LocalCache\local-packages\Python39\site-packages\pandas\core\apply.py:1098: RuntimeWarning:

All-NaN slice encountered



In [60]:
max_increase = max_increase.to_frame().reset_index()

In [61]:
max_decrease = max_decrease.to_frame().reset_index()

In [62]:
px.strip(data_frame=max_increase, x="continent", y="14d-incidence", color="countries")

In [63]:
px.strip(data_frame=max_decrease, x="continent", y="14d-incidence", color="countries")

Which country showed the highest/lowest fluctuation in `14d-incidence` within a year?

In [64]:
difference_14d = cdf_group["14d-incidence"].apply(np.max, axis=0) - cdf_group["14d-incidence"].apply(np.min, axis=0)
difference_14d_sorted_max = difference_14d.sort_values(ascending=False)
difference_14d_sorted_min = difference_14d.sort_values(ascending=True)
difference_14d_sorted_max.index[0], difference_14d_sorted_min.index[0]

(('Europe', 'Andorra'), ('Asia', 'Laos'))

Create a line plot showing the `14-incidence` for all European countries. Use `groupby` operation to generate the data list for the plotly plot. 

In [65]:
cdf_for_plot = cdf.set_index('continent')
europe = cdf_for_plot.loc['Europe',]
fig = px.line(europe, x='date_reported', y='14d-incidence', color='countries')
fig.show()

Create a smoothed version of the `14d-incidence` by averaging 3 months.

In [66]:
from collections import deque

def sliding_window_function(df):
    sliding_window = deque([], maxlen = 90)
    mean_values = []
    for x in df["14d-incidence"]:
        sliding_window.append(x)
        mean_w = np.mean(list(sliding_window))
        mean_values.append(mean_w)
    df["smoothed_incidence"] = mean_values
    return df

europe_countries = europe.groupby("countries")

europe_countries = europe_countries.apply(sliding_window_function)
europe_countries.head()

countries        date  day  month  year  cases  deaths 2lettercode  \
continent                                                                      
Europe      Albania  14/12/2020   14     12  2020    788      14          AL   
Europe      Albania  13/12/2020   13     12  2020    879      12          AL   
Europe      Albania  12/12/2020   12     12  2020    802      12          AL   
Europe      Albania  11/12/2020   11     12  2020    873      14          AL   
Europe      Albania  10/12/2020   10     12  2020    752      15          AL   

          3lettercode  population  14d-incidence date_reported  \
continent                                                        
Europe            ALB     2862427     380.970414    2020-12-14   
Europe            ALB     2862427     382.612378    2020-12-13   
Europe            ALB     2862427     370.943958    2020-12-12   
Europe            ALB     2862427     365.459102    2020-12-11   
Europe            ALB     2862427     357.878122    2020-12-10   

          deltaTime_since_start_of_recording  smoothed_incidence  
continent                                                         
Europe                              349 days          380.970414  
Europe                              348 days          381.791396  
Europe                              347 days          378.175583  
Europe                              346 days          374.996463  
Europe                              345 days          371.572795

In [67]:
fig = px.line(europe_countries, x ="date_reported", y="smoothed_incidence", color="countries")
fig.show()

Create a radial plot of death rate / 100000 people (see popData2019), where one year completes a circle, i.e. 360˚. Visualize the recored years for Italy, Germany, Sweden and Greece. Hint you might need to turn the dateTime into `day within the year` (%j) and adjust 365 to 360 degrees. 

In [68]:
europe['death_rate'] = europe['deaths']/europe['population']*100_000
europe = europe.groupby("countries")

C:\Users\L\AppData\Local\Temp/ipykernel_14532/991040398.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [69]:
europe_only_4 = pd.concat(europe.get_group(name) for name in ['Italy', 'Germany', 'Sweden', 'Greece'])

In [70]:
europe_only_4 = pd.concat(europe.get_group(name) for name in ['Italy', 'Germany', 'Sweden', 'Greece'])

europe_only_4.reset_index()
europe_only_4['deltaTime_plot'] = europe_only_4['deltaTime_since_start_of_recording'].dt.days
fig = px.line_polar(europe_only_4, r='death_rate', theta='deltaTime_plot', color='countries', line_close = True)
fig.show()

Optional: Find "regular" mortality rates for those countries and visualize it in the plot as well.

In [71]:
# find on the same website